In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/notebook-1/__results__.html
/kaggle/input/notebook-1/__notebook__.ipynb
/kaggle/input/notebook-1/__output__.json
/kaggle/input/notebook-1/custom.css
/kaggle/input/notebook-1/product_images/21ixQ8jLBQL.jpg
/kaggle/input/notebook-1/product_images/71xunEb3cbL.jpg
/kaggle/input/notebook-1/product_images/41VRx0XzLGL.jpg
/kaggle/input/notebook-1/product_images/61AQCAZNF-L.jpg
/kaggle/input/notebook-1/product_images/814ZQfPAw1L.jpg
/kaggle/input/notebook-1/product_images/61V13hQQjuL.jpg
/kaggle/input/notebook-1/product_images/51KWtmmnxKL.jpg
/kaggle/input/notebook-1/product_images/810uO75o3pL.jpg
/kaggle/input/notebook-1/product_images/81J69LvFzrL.jpg
/kaggle/input/notebook-1/product_images/71eVs4lefiL.jpg
/kaggle/input/notebook-1/product_images/51nO1t6FmaL.jpg
/kaggle/input/notebook-1/product_images/81L1XiXl4zL.jpg
/kaggle/input/notebook-1/product_images/61d-DO1m-bL.jpg
/kaggle/input/notebook-1/product_images/71Wmi6NyvwL.jpg
/kaggle/input/notebook-1/product_images/61zrJkifkKL.j

In [2]:
!pip uninstall -y transformers sentence-transformers tokenizers

Found existing installation: transformers 4.53.3
Uninstalling transformers-4.53.3:
  Successfully uninstalled transformers-4.53.3
Found existing installation: sentence-transformers 4.1.0
Uninstalling sentence-transformers-4.1.0:
  Successfully uninstalled sentence-transformers-4.1.0
Found existing installation: tokenizers 0.21.2
Uninstalling tokenizers-0.21.2:
  Successfully uninstalled tokenizers-0.21.2


In [3]:
!pip install sentence-transformers==3.0.1 transformers==4.44.0 tokenizers==0.19.1 --no-deps --quiet


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 82.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 74.8 MB/s eta 0:00:00


In [4]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')

/usr/local/lib/python3.11/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
2025-10-11 15:52:30.999029: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1760197951.432705      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1760197951.568090      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [5]:
!pip install faiss-cpu

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 62.5 MB/s eta 0:00:00


In [6]:
import torch
from torchvision import transforms
from PIL import Image
from tqdm import tqdm
import timm
from pathlib import Path
import urllib.parse
import faiss
from sklearn.preprocessing import normalize

/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'repr' attribute with value False was provided to the `Field()` function, which has no effect in the context it was used. 'repr' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` statement was used, or if the `Field()` function was attached to a single member of a union type.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:2225: UnsupportedFieldAttributeWarning: The 'frozen' attribute with value True was provided to the `Field()` function, which has no effect in the context it was used. 'frozen' is field-specific metadata, and can only be attached to a model field using `Annotated` metadata or by assignment. This may have happened because an `Annotated` type alias using the `type` 

In [7]:
INPUT_DIR_PROCESSED_CSVS = '/kaggle/input/Feature-Extraction'
INPUT_DIR_IMAGES = '/kaggle/input/Notebook-1'
OUTPUT_DIR = '/kaggle/working/'


In [8]:
PROCESSED_TRAIN_PATH = os.path.join(INPUT_DIR_PROCESSED_CSVS, 'processed_train.csv')
PROCESSED_TEST_PATH = os.path.join(INPUT_DIR_PROCESSED_CSVS, 'processed_test.csv')
IMAGE_EMBEDDINGS_TRAIN_PATH = os.path.join(OUTPUT_DIR, 'image_embeddings_train.npy')
IMAGE_EMBEDDINGS_TEST_PATH = os.path.join(OUTPUT_DIR, 'image_embeddings_test.npy')
TEXT_EMBEDDINGS_TRAIN_PATH = os.path.join(OUTPUT_DIR, 'text_embeddings_train.npy')
TEXT_EMBEDDINGS_TEST_PATH = os.path.join(OUTPUT_DIR, 'text_embeddings_test.npy')
KNN_FEATURES_TRAIN_PATH = os.path.join(OUTPUT_DIR, 'knn_features_train.csv')
KNN_FEATURES_TEST_PATH = os.path.join(OUTPUT_DIR, 'knn_features_test.csv')


In [9]:
def get_filename_from_url(url):
    if not isinstance(url, str):
        return None
    try:
        return Path(urllib.parse.unquote(Path(url).name)).name
    except Exception:
        return url.split('/')[-1]

In [10]:
def generate_image_embeddings(df, image_folder, model):
    
    model.eval()
    
    transform = transforms.Compose([
        transforms.Resize((CONFIG["image_size"], CONFIG["image_size"])),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
    ])
    
    df['image_filename'] = df['image_link'].apply(get_filename_from_url)
    all_embeddings = []
    
    for i in tqdm(range(0, len(df), CONFIG["batch_size"]), desc="Generating Image Embeddings"):
        batch_df = df.iloc[i:i+CONFIG["batch_size"]]
        batch_images = []
        
        for filename in batch_df['image_filename']:
            real_filename = f"product_images/{str(filename)}"
            image_path = os.path.join(image_folder, real_filename)
            try:
                image = Image.open(image_path).convert("RGB")
                image = transform(image)
                batch_images.append(image)
            except (FileNotFoundError, IOError):
                batch_images.append(torch.zeros((3, CONFIG["image_size"], CONFIG["image_size"])))

        if batch_images:
            batch_tensor = torch.stack(batch_images).to(CONFIG["device"])
            with torch.no_grad():
                embeddings = model.forward_features(batch_tensor)
                embeddings = embeddings.mean(dim=[2, 3]) 
            all_embeddings.append(embeddings.cpu().numpy())

    return np.vstack(all_embeddings)

In [11]:
def generate_text_embeddings(df, model):
    sentences = df['cleaned_content'].fillna('').tolist()
    embeddings = model.encode(sentences, show_progress_bar=False, device=CONFIG["device"], batch_size=CONFIG["batch_size"])
    return embeddings


In [12]:
def generate_knn_features(train_img_emb, train_txt_emb, test_img_emb, test_txt_emb, train_prices):
    train_embeddings = np.concatenate([normalize(train_img_emb), normalize(train_txt_emb)], axis=1)
    test_embeddings = np.concatenate([normalize(test_img_emb), normalize(test_txt_emb)], axis=1)
    index = faiss.IndexFlatL2(train_embeddings.shape[1])
    index.add(train_embeddings.astype('float32'))
    distances, indices = index.search(train_embeddings.astype('float32'), CONFIG["knn_neighbors"])
    test_distances, test_indices = index.search(test_embeddings.astype('float32'), CONFIG["knn_neighbors"])
    def create_features_from_neighbors(neighbor_indices, neighbor_distances, price_source):
        neighbor_prices = price_source[neighbor_indices]
        features = {
            'knn_mean_price': np.mean(neighbor_prices, axis=1),
            'knn_std_price': np.std(neighbor_prices, axis=1),
            'knn_min_price': np.min(neighbor_prices, axis=1),
            'knn_max_price': np.max(neighbor_prices, axis=1),
            'knn_median_price': np.median(neighbor_prices, axis=1),
            'knn_mean_dist': np.mean(neighbor_distances, axis=1),
        }
        return pd.DataFrame(features)
    train_knn_features = create_features_from_neighbors(indices, distances, train_prices)
    test_knn_features = create_features_from_neighbors(test_indices, test_distances, train_prices)
    return train_knn_features, test_knn_features

In [13]:
train_df = pd.read_csv('/kaggle/input/feature-extraction/processed_train.csv')
test_df = pd.read_csv('/kaggle/input/feature-extraction/processed_test.csv')

In [14]:
CONFIG = {
    "image_model_name": "efficientnet_b0",
    "image_size": 224,
    "batch_size": 64,
    "device": "cuda" if torch.cuda.is_available() else "cpu",
    "knn_neighbors": 10,
}

In [15]:
image_model = timm.create_model(CONFIG["image_model_name"], pretrained=True, num_classes=0).to(CONFIG["device"])
train_image_embeddings = generate_image_embeddings(train_df, INPUT_DIR_IMAGES, image_model)
np.save(IMAGE_EMBEDDINGS_TRAIN_PATH, train_image_embeddings)

model.safetensors:   0%|          | 0.00/21.4M [00:00<?, ?B/s]

Generating Image Embeddings: 100%|██████████| 1172/1172 [01:56<00:00, 10.03it/s]


In [16]:
test_image_embeddings = generate_image_embeddings(test_df, INPUT_DIR_IMAGES, image_model)
np.save(IMAGE_EMBEDDINGS_TEST_PATH, test_image_embeddings)


Generating Image Embeddings: 100%|██████████| 1172/1172 [01:42<00:00, 11.46it/s]


In [17]:
train_text_embeddings = generate_text_embeddings(train_df,model)

In [18]:
np.save(TEXT_EMBEDDINGS_TRAIN_PATH, train_text_embeddings)

In [19]:
test_text_embeddings = generate_text_embeddings(test_df, model)
np.save(TEXT_EMBEDDINGS_TEST_PATH, test_text_embeddings)

In [20]:
train_knn_df, test_knn_df = generate_knn_features(
        train_image_embeddings, train_text_embeddings,
        test_image_embeddings, test_text_embeddings,
        train_df['price'].values
    )

In [21]:
train_knn_df.to_csv(KNN_FEATURES_TRAIN_PATH, index=False)
test_knn_df.to_csv(KNN_FEATURES_TEST_PATH, index=False)

In [22]:
!ls /kaggle/working/

image_embeddings_test.npy   knn_features_train.csv    text_embeddings_train.npy
image_embeddings_train.npy  __notebook__.ipynb
knn_features_test.csv	    text_embeddings_test.npy


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
